In [1]:
from recogym import Configuration

import numpy as np
from numpy.random import choice
from recogym.agents import Agent

class CFAgent(Agent):

    def __init__(self, config):
        
        super(CFAgent, self).__init__(config) # Set number of products as an attribute of the Agent.

        self.organic_views = np.zeros(self.config.num_products) # Track number of times each item viewed in Organic session.

        self.act_counter = 0
        self.train_counter = 0

    def train(self, observation, action, reward, done):

        # Train method learns from a tuple of data. This method can be called for offline or online learning
        # Adding organic session to organic view counts.

        if observation:
            
            for session in observation.sessions(): # -- LOOP

                print("\n-------------- TRAIN START --------------")
                print(f"train () {self.train_counter} :::: reward {reward}")

                self.organic_views[session['v']] += 1

                print(f"train () {self.train_counter} :::: self.organic_views {self.organic_views}")

                self.train_counter +=1

                print("-------------- TRAIN END --------------\n")

    def act(self, observation, reward, done):

        print("\n-------------- ACT START --------------")

        # An act method takes in an observation, which could either be `None` or an Organic_Session
        # and returns a integer between 0 and num_products indicating which product the agent recommends.

        print(f"act () {self.act_counter} :::: get reward {reward}")
        print(f"act () {self.act_counter} :::: get observation sessions {observation.sessions()}")
        print(f"act () {self.act_counter} :::: have organic_views {self.organic_views}")
        print(f"act () {self.act_counter} :::: have sum(self.organic_views) {sum(self.organic_views)}")

        prob = self.organic_views / sum(self.organic_views)

        print(f"act () {self.act_counter} :::: calc prob {prob}")

        print(f"act () {self.act_counter} :::: have num_products {num_products}")

        # Choosing action randomly in proportion with number of views.

        action = choice(self.config.num_products, p = prob) # GENERATE ACTION ONLINE

        print(f"act () {self.act_counter} :::: return action {action}")
        print(f"act () {self.act_counter} :::: return prob[action] {prob[action]}")

        self.act_counter += 1

        print("-------------- ACT END --------------\n")

        return {
            **super().act(observation, reward, done),
            **{
                'a': action,
                'ps': prob[action]
            }
        }

In [2]:
import gym
from recogym import env_1_args

env_1_args['random_seed'] = 42

env_1_args['num_steps'] = 10

env = gym.make('reco-gym-v1')

env.init_gym(env_1_args)

# Instantiate instance of CFAgent class.

num_products = 10

num_offline_users = 5
num_online_users = 5

cf_agent = CFAgent(Configuration({
    **env_1_args,
    'num_products': num_products,
}))

# Resets random seed back to 42, or whatever we set it to in env_0_args.

env.reset_random_seed()

num_clicks, num_events = 0, 0

# ****** TRAIN OFFLINE ******

unique_offline_user_id = 0

for _ in range(num_offline_users):

    # Reset env and set done to False.

    unique_offline_user_id += 1

    env.reset()
    done = False
    observation, reward, done = None, 0, False

    while not done: # ----- LOOP

        old_observation = observation

        action, observation, reward, done, info = env.step_offline(observation, reward, done)

        cf_agent.train(old_observation, action, reward, done) # TRAIN OFFLINE

# ****** TRAIN ONLINE ******

unique_online_user_id = 0

for _ in range(num_online_users):

    # Reset env and set done to False.

    unique_online_user_id += 1

    env.reset(unique_online_user_id)

    observation, _, done, _ = env.step(None)
    reward = None

    while not done: # ----- LOOP
        
        print("\n========================== ONLINE LOOP START ===========================")

        print(f"ONLINE %%%% RUN act() obs sessions {observation.sessions()}")

        action = cf_agent.act(observation, reward, done) # create recommendation product id

        print(f"ONLINE %%%% action {action}, obs sessions {observation.sessions()} --> RUN step()")

        observation, reward, done, info = env.step(action['a'])

        print(f"ONLINE %%%% calc obs sessions {observation.sessions()}, reward {reward}")

        # Used for calculating click through rate.

        num_clicks += 1 if reward == 1 and reward is not None else 0
        num_events += 1
        
        print(f"ONLINE %%%% num_clicks: {num_clicks}")
        print(f"ONLINE %%%% num_events: {num_events}")
        print(f"ONLINE %%%% CTR {num_clicks / num_events}")
        
        print("============================== ONLINE LOOP END ============================\n")

ctr = num_clicks / num_events

# ------------------------------------

print(f"TOTAL num_clicks: {num_clicks}")
print(f"TOTAL num_events: {num_events}")
print(f"TOTAL Click Through Rate: {ctr:.4f}")



step_offline ---- START done False
step () ---- START action_id None
step () ---- FIRST STEP => RUN generate_organic_sessions()
generate_organic_sessions () INIT - state 0
update_product_view () ---- START, 
omega [[ 0.49671415]
 [-0.1382643 ]
 [ 0.64768854]
 [ 1.52302986]
 [-0.23415337]], 
gamma [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.91328024 -1.72491783]
 [-0.56228753 -1.01283112  0.31424733 -0.90802408 -1.4123037 ]
 [ 1.46564877 -0.2257763   0.0675282  -1.42474819 -0.54438272]
 [ 0.11092259 -1.15099358  0.37569802 -0.60063869 -0.29169375]
 [-0.60170661  1.85227818 -0.01349722 -1.05771093  0.82254491]
 [-1.22084365  0.2088636  -1.95967012 -1.32818605  0.19686124]
 [ 0.73846658  0.17136828 -0.11564828 -0.3011037  -1.47852199]
 [-0.71984421 -0.46063877  1.05712223  0.34361829 -1.76304016]], 
beta [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 

 [-0.71984421 -0.46063877  1.05712223  0.34361829 -1.76304016]]
draw_click () ---- cached_state_seed [-2.96699295  4.5981963   0.46235256  1.13453518  4.98163826  1.89850636
  5.00703687  1.80687302  0.17419961  0.65963157]
draw_click () ---- ctr [0.00652879 0.01805574 0.01008924 0.01116989 0.01883431 0.01254282
 0.01888522 0.01237086 0.00966572 0.01039314]
draw_click () ---- ctr[recommendation] 0.01805574201938246
draw_click () ---- return click 0, recommendation 1
step () ---- reward 0 from action_id 1
update_state () ---- old state 1, 
omega [[-0.47022256]
 [ 2.06323369]
 [ 0.89332042]
 [-2.47311541]
 [ 0.99239178]], 
gamma [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.91328024 -1.72491783]
 [-0.56228753 -1.01283112  0.31424733 -0.90802408 -1.4123037 ]
 [ 1.46564877 -0.2257763   0.0675282  -1.42474819 -0.54438272]
 [ 0.11092259 -1.15099358  0.37569802 -0.60063869 

 [-0.71984421 -0.46063877  1.05712223  0.34361829 -1.76304016]]
step () ---- state 1
step () ---- state 1
step_offline ---- return action {'t': 19, 'u': 0, 'a': 4, 'ps': 0.1, 'ps-a': ()}, obs sessions [], done False
step_offline ---- START done False
step_offline ---- get obs sessions [], reward 0
step () ---- START action_id 4
draw_click () ---- recommendation 4, 
omega [[ 0.25607383]
 [-0.68140955]
 [ 0.13218048]
 [ 0.86343217]
 [ 1.22163181]], 
gamma [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.91328024 -1.72491783]
 [-0.56228753 -1.01283112  0.31424733 -0.90802408 -1.4123037 ]
 [ 1.46564877 -0.2257763   0.0675282  -1.42474819 -0.54438272]
 [ 0.11092259 -1.15099358  0.37569802 -0.60063869 -0.29169375]
 [-0.60170661  1.85227818 -0.01349722 -1.05771093  0.82254491]
 [-1.22084365  0.2088636  -1.95967012 -1.32818605  0.19686124]
 [ 0.73846658  0.17136828 -0.11564828 

draw_click () ---- ctr [0.01171893 0.00702676 0.00534176 0.01019022 0.0071617  0.01359673
 0.00636883 0.01012796 0.00636927 0.01295294]
draw_click () ---- ctr[recommendation] 0.0071617049800360676
draw_click () ---- return click 0, recommendation 4
step () ---- reward 0 from action_id 4
update_state () ---- old state 1, 
omega [[-1.91393178]
 [-1.00778035]
 [-0.30452598]
 [ 1.21559189]
 [ 1.56036866]], 
gamma [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.91328024 -1.72491783]
 [-0.56228753 -1.01283112  0.31424733 -0.90802408 -1.4123037 ]
 [ 1.46564877 -0.2257763   0.0675282  -1.42474819 -0.54438272]
 [ 0.11092259 -1.15099358  0.37569802 -0.60063869 -0.29169375]
 [-0.60170661  1.85227818 -0.01349722 -1.05771093  0.82254491]
 [-1.22084365  0.2088636  -1.95967012 -1.32818605  0.19686124]
 [ 0.73846658  0.17136828 -0.11564828 -0.3011037  -1.47852199]
 [-0.71984421 -0.460

 [-0.71984421 -0.46063877  1.05712223  0.34361829 -1.76304016]]
update_state () ---- new state 1, 
omega [[-1.93764924]
 [-1.36542142]
 [ 0.0023146 ]
 [ 1.22640857]
 [ 1.62155103]], 
gamma [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.91328024 -1.72491783]
 [-0.56228753 -1.01283112  0.31424733 -0.90802408 -1.4123037 ]
 [ 1.46564877 -0.2257763   0.0675282  -1.42474819 -0.54438272]
 [ 0.11092259 -1.15099358  0.37569802 -0.60063869 -0.29169375]
 [-0.60170661  1.85227818 -0.01349722 -1.05771093  0.82254491]
 [-1.22084365  0.2088636  -1.95967012 -1.32818605  0.19686124]
 [ 0.73846658  0.17136828 -0.11564828 -0.3011037  -1.47852199]
 [-0.71984421 -0.46063877  1.05712223  0.34361829 -1.76304016]], 
beta [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.913280

...

 [-0.71984421 -0.46063877  1.05712223  0.34361829 -1.76304016]]
update_state () ---- new state 1, 
omega [[-1.22755667]
 [ 0.61813716]
 [ 0.48359897]
 [ 0.2787908 ]
 [ 0.85712029]], 
gamma [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.91328024 -1.72491783]
 [-0.56228753 -1.01283112  0.31424733 -0.90802408 -1.4123037 ]
 [ 1.46564877 -0.2257763   0.0675282  -1.42474819 -0.54438272]
 [ 0.11092259 -1.15099358  0.37569802 -0.60063869 -0.29169375]
 [-0.60170661  1.85227818 -0.01349722 -1.05771093  0.82254491]
 [-1.22084365  0.2088636  -1.95967012 -1.32818605  0.19686124]
 [ 0.73846658  0.17136828 -0.11564828 -0.3011037  -1.47852199]
 [-0.71984421 -0.46063877  1.05712223  0.34361829 -1.76304016]], 
beta [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.913280

 [-0.71984421 -0.46063877  1.05712223  0.34361829 -1.76304016]]
update_state () ---- new state 1, 
omega [[-1.51142952]
 [ 0.4773246 ]
 [ 0.66990892]
 [ 0.26542914]
 [ 1.30320838]], 
gamma [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.91328024 -1.72491783]
 [-0.56228753 -1.01283112  0.31424733 -0.90802408 -1.4123037 ]
 [ 1.46564877 -0.2257763   0.0675282  -1.42474819 -0.54438272]
 [ 0.11092259 -1.15099358  0.37569802 -0.60063869 -0.29169375]
 [-0.60170661  1.85227818 -0.01349722 -1.05771093  0.82254491]
 [-1.22084365  0.2088636  -1.95967012 -1.32818605  0.19686124]
 [ 0.73846658  0.17136828 -0.11564828 -0.3011037  -1.47852199]
 [-0.71984421 -0.46063877  1.05712223  0.34361829 -1.76304016]], 
beta [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.913280

 [-0.71984421 -0.46063877  1.05712223  0.34361829 -1.76304016]]
draw_click () ---- cached_state_seed [ 0.66931304  0.73195382 -3.49756527  0.9241329  -0.07721876  2.06798745
 -0.33408085 -0.37664543 -1.7846618   2.84691308]
draw_click () ---- ctr [0.01040834 0.01050735 0.00621954 0.01081803 0.00931613 0.01286553
 0.00897816 0.00892402 0.00741796 0.0144141 ]
draw_click () ---- ctr[recommendation] 0.014414104632757479
draw_click () ---- return click 0, recommendation 9
step () ---- reward 0 from action_id 9
update_state () ---- old state 1, 
omega [[-1.55436416]
 [ 0.33256186]
 [ 0.68768804]
 [ 0.20651666]
 [ 1.04556023]], 
gamma [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.91328024 -1.72491783]
 [-0.56228753 -1.01283112  0.31424733 -0.90802408 -1.4123037 ]
 [ 1.46564877 -0.2257763   0.0675282  -1.42474819 -0.54438272]
 [ 0.11092259 -1.15099358  0.37569802 -0.60063869

 [-0.71984421 -0.46063877  1.05712223  0.34361829 -1.76304016]]
update_state () ---- new state 0, 
omega [[-1.69836566]
 [ 0.18135967]
 [ 0.75521386]
 [ 0.42993803]
 [ 0.79578439]], 
gamma [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.91328024 -1.72491783]
 [-0.56228753 -1.01283112  0.31424733 -0.90802408 -1.4123037 ]
 [ 1.46564877 -0.2257763   0.0675282  -1.42474819 -0.54438272]
 [ 0.11092259 -1.15099358  0.37569802 -0.60063869 -0.29169375]
 [-0.60170661  1.85227818 -0.01349722 -1.05771093  0.82254491]
 [-1.22084365  0.2088636  -1.95967012 -1.32818605  0.19686124]
 [ 0.73846658  0.17136828 -0.11564828 -0.3011037  -1.47852199]
 [-0.71984421 -0.46063877  1.05712223  0.34361829 -1.76304016]], 
beta [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.913280

act () 652 :::: get observation sessions []
act () 652 :::: have organic_views [ 3.  3.  0.  0. 18.  9.  3.  2.  0.  5.]
act () 652 :::: have sum(self.organic_views) 43.0
act () 652 :::: calc prob [0.06976744 0.06976744 0.         0.         0.41860465 0.20930233
 0.06976744 0.04651163 0.         0.11627907]
act () 652 :::: have num_products 10
act () 652 :::: return action 5
act () 652 :::: return prob[action] 0.20930232558139536
-------------- ACT END --------------

ONLINE %%%% action {'t': 219, 'u': 5, 'a': 5, 'ps': 0.20930232558139536}, obs sessions [] --> RUN step()
step () ---- START action_id 5
draw_click () ---- recommendation 5, 
omega [[-2.07301978]
 [ 0.59681524]
 [ 0.90574248]
 [ 0.76229815]
 [ 1.04676968]], 
gamma [[ 0.49671415 -0.1382643   0.64768854  1.52302986 -0.23415337]
 [-0.23413696  1.57921282  0.76743473 -0.46947439  0.54256004]
 [-0.46341769 -0.46572975  0.24196227 -1.91328024 -1.72491783]
 [-0.56228753 -1.01283112  0.31424733 -0.90802408 -1.4123037 ]
 [ 1.46564